In [2]:
import numpy as np
import pandas as pd
import random
import hashlib
import secrets

In [3]:
def generate_normal_data(mu, n):
    sigma = random.random() / 3
    return np.random.normal(mu/10, sigma, n)

def random_id():
    random_bytes = secrets.token_bytes(32)
    hash_object = hashlib.sha256()
    hash_object.update(random_bytes)
    return hash_object.hexdigest()[:24]

In [16]:
tests = [-1, 0, 2]
datasets = [3, 7, 1, 5]

f = open("test.log", "w")

data = []
for test in tests:
    test_uuid = random_id()[:4]
    for dataset in datasets:
        mu = (test + dataset)
        count = random.randint(500, 2000)
        answer_relevance_scores = generate_normal_data(mu + 0, count)
        groundedness_scores = generate_normal_data(mu + 1, count)
        answer_correctness_scores = generate_normal_data(mu + 2, count)
        context_relevance_scores = generate_normal_data(mu + 3, count)

        f.write(f"test: {test}, dataset: {dataset}, should have:\n")
        f.write(f"\t Answer Correctness scores centered around {(mu+2)/10}\n")
        f.write(f"\t Answer Relevance scores centered around {(mu+0)/10}\n")
        f.write(f"\t Context Relevance scores centered around {(mu+3)/10}\n")
        f.write(f"\t Grounded-ness scores centered around {(mu+1)/10}\n")
        f.write("\n")

        for i in range(count):
            data.append({
                'record_id' : random_id(),
                'answer_relevance': answer_relevance_scores[i],
                'groundedness': groundedness_scores[i],
                'answer_correctness': answer_correctness_scores[i],
                'context_relevance': context_relevance_scores[i],
                'latency': 0,
                'test': f"test_{test}",
                'test_uuid': test_uuid,
                'dataset': f"dataset_{dataset}",
            })
f.close()

df = pd.DataFrame(data)
df.to_parquet("test.parquet")

In [10]:
import sys, os
sys.path.append(f"{os.getcwd()}/../..")
import tru_analysis

In [17]:
tru_analysis.box_plot_by_metric("test.parquet")

In [19]:
tru_analysis.box_plot_by_dataset("test.parquet")